In [34]:
# importing libraries
import numpy as np
import pandas as pd
from pathlib import Path
import hvplot.pandas
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
import time
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.metrics import MeanSquaredError
from pandas.tseries.offsets import DateOffset
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split

In [2]:
all_values = pd.read_csv(Path("Resources/all_values_superset.csv"))
all_values['date'] = pd.to_datetime(all_values['date'], format='%Y-%m')
all_values.set_index('date', inplace=True)
# all_values.drop(columns=['All-items 8', 'All-items excluding food', 'All-items excluding food and energy', 'Clothing and footwear'], inplace=True)
all_values.drop(columns=['All-items 8', 'All-items excluding food', 'All-items excluding food and energy'], inplace=True)
all_values.dtypes

Composite_Benchmark_SA_BANCROFT_AND_AREA                           float64
Single_Family_Benchmark_SA_BANCROFT_AND_AREA                       float64
One_Storey_Benchmark_SA_BANCROFT_AND_AREA                          float64
Two_Storey_Benchmark_SA_BANCROFT_AND_AREA                          float64
Composite_Benchmark_SA_BARRIE_AND_AREA                             float64
                                                                    ...   
Clothing and footwear                                              float64
Transportation                                                     float64
Health and personal care                                           float64
Recreation, education and reading                                  float64
Alcoholic beverages, tobacco products and recreational cannabis    float64
Length: 174, dtype: object

In [3]:
scaler_all = StandardScaler()
all_scaler = scaler_all.fit(all_values)
all_values_scaled = all_scaler.transform(all_values)

all_values_scaled_df = pd.DataFrame(all_values_scaled, columns=all_values.columns, index=all_values.index)
all_values_scaled_df.head()

Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                   
2008-06-01                                 -0.825918   
2008-07-01                                 -0.831709   
2008-08-01                                 -0.846185   
2008-09-01                                 -0.865487   
2008-10-01                                 -0.872242   

            Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                       
2008-06-01                                     -0.825918   
2008-07-01                                     -0.831709   
2008-08-01                                     -0.846185   
2008-09-01                                     -0.865487   
2008-10-01                                     -0.872242   

            One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.947581   
2008-07-01                                  -0.973779   
2008-08-01                                  -0.985006   
2008-09-01                                  -1.015882   
2008-10-01                                  -1.023367   

            Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.407433   
2008-07-01                                  -0.374424   
2008-08-01                                  -0.384427   
2008-09-01                                  -0.346415   
2008-10-01                                  -0.328410   

            Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.936442   
2008-07-01                               -0.943571   
2008-08-01                               -0.950192   
2008-09-01                               -0.948155   
2008-10-01                               -0.951720   

            Single_Family_Benchmark_SA_BARRIE_AND_AREA  \
date                                                     
2008-06-01                                   -0.935664   
2008-07-01                                   -0.943884   
2008-08-01                                   -0.951622   
2008-09-01                                   -0.949687   
2008-10-01                                   -0.952105   

            One_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.932140   
2008-07-01                                -0.953696   
2008-08-01                                -0.970121   
2008-09-01                                -0.964988   
2008-10-01                                -0.956263   

            Two_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.938398   
2008-07-01                                -0.937469   
2008-08-01                                -0.938862   
2008-09-01                                -0.940254   
2008-10-01                                -0.948142   

            Townhouse_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.823496   
2008-07-01                               -0.817839   
2008-08-01                               -0.812889   
2008-09-01                               -0.811475   
2008-10-01                               -0.815011   

            Apartment_Benchmark_SA_BARRIE_AND_AREA  ...       ITB  Bank Rate  \
date                                                ...                        
2008-06-01                               -0.888138  ... -0.804832   2.568481   
2008-07-01                               -0.880624  ... -0.865314   2.568481   
2008-08-01                               -0.869769  ... -0.862638   2.568481   
2008-09-01                               -0.863925  ... -0.69

In [4]:
targets = [col for col in all_values_scaled_df.columns.tolist() if col.find('Benchmark') > 0]

In [5]:
y = all_values_scaled_df[targets]

In [6]:
X = all_values_scaled_df.drop(columns = targets)

In [7]:
y.shape

(176, 161)

In [8]:
y.head()

Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                   
2008-06-01                                 -0.825918   
2008-07-01                                 -0.831709   
2008-08-01                                 -0.846185   
2008-09-01                                 -0.865487   
2008-10-01                                 -0.872242   

            Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                       
2008-06-01                                     -0.825918   
2008-07-01                                     -0.831709   
2008-08-01                                     -0.846185   
2008-09-01                                     -0.865487   
2008-10-01                                     -0.872242   

            One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.947581   
2008-07-01                                  -0.973779   
2008-08-01                                  -0.985006   
2008-09-01                                  -1.015882   
2008-10-01                                  -1.023367   

            Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.407433   
2008-07-01                                  -0.374424   
2008-08-01                                  -0.384427   
2008-09-01                                  -0.346415   
2008-10-01                                  -0.328410   

            Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.936442   
2008-07-01                               -0.943571   
2008-08-01                               -0.950192   
2008-09-01                               -0.948155   
2008-10-01                               -0.951720   

            Single_Family_Benchmark_SA_BARRIE_AND_AREA  \
date                                                     
2008-06-01                                   -0.935664   
2008-07-01                                   -0.943884   
2008-08-01                                   -0.951622   
2008-09-01                                   -0.949687   
2008-10-01                                   -0.952105   

            One_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.932140   
2008-07-01                                -0.953696   
2008-08-01                                -0.970121   
2008-09-01                                -0.964988   
2008-10-01                                -0.956263   

            Two_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.938398   
2008-07-01                                -0.937469   
2008-08-01                                -0.938862   
2008-09-01                                -0.940254   
2008-10-01                                -0.948142   

            Townhouse_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.823496   
2008-07-01                               -0.817839   
2008-08-01                               -0.812889   
2008-09-01                               -0.811475   
2008-10-01                               -0.815011   

            Apartment_Benchmark_SA_BARRIE_AND_AREA  ...  \
date                                                ...   
2008-06-01                               -0.888138  ...   
2008-07-01                               -0.880624  ...   
2008-08-01                               -0.869769  ...   
2008-09-01                               -0.863925  ...   
2008-10-01                               -0.898157  ...   

            Single_Family_Benchmark_SA_WINDSOR_

In [9]:
X.head()

Lumber      Wood       XHB       ITB  Bank Rate      Food  \
date                                                                      
2008-06-01 -0.664592 -0.505146 -0.929491 -0.804832   2.568481 -1.744835   
2008-07-01 -0.637850 -0.524583 -1.017591 -0.865314   2.568481 -1.689366   
2008-08-01 -0.605399 -0.486888 -0.959232 -0.862638   2.568481 -1.633897   
2008-09-01 -0.720345 -0.442713 -0.811089 -0.690289   2.568481 -1.550693   
2008-10-01 -0.881425 -0.780796 -0.937908 -0.775928   1.604616 -1.516025   

             Shelter  Household operations, furnishings and equipment  \
date                                                                    
2008-06-01 -1.183779                                        -1.929083   
2008-07-01 -1.099725                                        -1.901250   
2008-08-01 -1.057698                                        -1.901250   
2008-09-01 -1.116536                                        -1.776002   
2008-10-01 -1.108130                                        -1.803835   

            Clothing and footwear  Transportation  Health and personal care  \
date                                                                          
2008-06-01               0.208160       -0.678934                 -1.897463   
2008-07-01               0.726901       -0.678934                 -1.884047   
2008-08-01               0.402688       -0.795051                 -1.763302   
2008-09-01               0.208160       -0.802309                 -1.776718   
2008-10-01              -0.634795       -1.092603                 -1.763302   

            Recreation, education and reading  \
date                                            
2008-06-01                          -1.378353   
2008-07-01                          -1.394462   
2008-08-01                          -1.346137   
2008-09-01                          -1.362245   
2008-10-01                          -1.394462   

            Alcoholic beverages, tobacco products and recreational cannabis  
date                                                                         
2008-06-01                                          -1.491493                
2008-07-01                                          -1.497273                
2008-08-01                                          -1.503054                
2008-09-01                                          -1.474150                
2008-10-01                                          -1.474150

In [10]:
all_values_scaled_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [11]:
X_train, X_test, y_train, y_test = train_test_split(X, y)
X_train
X_test.sort_index(ascending=True, inplace=True)
y_train
y_test.sort_index(ascending=True, inplace=True)
y_test_size = y_test.shape[0]
y_test_size

44

In [12]:
# Neural network parameters
n_input_feats = len(X.columns)

n_outputs = 161

# Trial 2
# hidden_nodes_layer1 = 512
# hidden_nodes_layer2 = 512
# hidden_nodes_layer3 = 256

# Trial 3
hidden_nodes_layer1 = 128
hidden_nodes_layer2 = 512
hidden_nodes_layer3 = 1024
# hidden_nodes_layer4 = 4
print(f"""
Neural Network Parameters:
--------------------------
Input Features: {n_input_feats}
Layers:         3
Layer1 Nodes:   {hidden_nodes_layer1}
Layer2 Nodes:   {hidden_nodes_layer2}
Layer3 Nodes:   {hidden_nodes_layer3}
Output Nodes:   {n_outputs}
""")


Neural Network Parameters:
--------------------------
Input Features: 13
Layers:         3
Layer1 Nodes:   128
Layer2 Nodes:   512
Layer3 Nodes:   1024
Output Nodes:   161



In [13]:
# define model
nn = Sequential()

2023-06-12 21:11:23.582298: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [14]:
# Add the first hidden layer
nn.add(Dense(
    units=hidden_nodes_layer1,
    input_dim = n_input_feats,
    activation='relu',
    name='hidden1'
))

In [15]:
# Add the second hidden layer
nn.add(Dense(
    units=hidden_nodes_layer2,
    activation='relu',
    name='hidden2'
))

In [16]:
# Add the third hidden layer
nn.add(Dense(
    units=hidden_nodes_layer3,
    activation='relu',
    name='hidden3'
))

In [17]:
# Add output
nn.add(Dense(
    n_outputs,
    activation='linear',
    name='output'
))

In [18]:
# Display the Sequential model summary
nn.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 hidden1 (Dense)             (None, 128)               1792      
                                                                 
 hidden2 (Dense)             (None, 512)               66048     
                                                                 
 hidden3 (Dense)             (None, 1024)              525312    
                                                                 
 output (Dense)              (None, 161)               165025    
                                                                 
Total params: 758,177
Trainable params: 758,177
Non-trainable params: 0
_________________________________________________________________


In [19]:
# Compile the Sequential model
nn.compile(loss='mean_squared_error', optimizer='adam', metrics=[MeanSquaredError()])

In [20]:
# Fit the model using 50 epochs and the training data
model = nn.fit(
    X_train,
    y_train,
    # batch_size=11,
    validation_split=0.2,
    epochs=100
)

Epoch 1/100
4/4 [==============================] - 1s 74ms/step - loss: 0.9093 - mean_squared_error: 0.9093 - val_loss: 0.4549 - val_mean_squared_error: 0.4549
Epoch 2/100
4/4 [==============================] - 0s 17ms/step - loss: 0.2785 - mean_squared_error: 0.2785 - val_loss: 0.1834 - val_mean_squared_error: 0.1834
Epoch 3/100
4/4 [==============================] - 0s 17ms/step - loss: 0.2025 - mean_squared_error: 0.2025 - val_loss: 0.0684 - val_mean_squared_error: 0.0684
Epoch 4/100
4/4 [==============================] - 0s 17ms/step - loss: 0.0940 - mean_squared_error: 0.0940 - val_loss: 0.1217 - val_mean_squared_error: 0.1217
Epoch 5/100
4/4 [==============================] - 0s 16ms/step - loss: 0.1166 - mean_squared_error: 0.1166 - val_loss: 0.0737 - val_mean_squared_error: 0.0737
Epoch 6/100
4/4 [==============================] - 0s 16ms/step - loss: 0.0698 - mean_squared_error: 0.0698 - val_loss: 0.0888 - val_mean_squared_error: 0.0888
Epoch 7/100
4/4 [=======================

In [37]:
nn = load_model(Path('./Models/trial3/nn_in13_relu128_relu512_relu1024_out161_r2score0.993962022788771.h5'))

In [38]:
# R2 score for training
train_pred = nn.predict(X_train)
training_r2 = r2_score(y_train.values, train_pred)
# model_loss, model_accuracy = nn.evaluate(X_test, y_test)
training_r2

5/5 [==============================] - 0s 2ms/step


0.9955071112085937

In [39]:
# Create a DataFrame with the history dictionary
model_df = pd.DataFrame(model.history, index=range(1, len(model.history["loss"]) + 1))

In [49]:
# Plot the accuracy
model_df[['mean_squared_error', 'val_mean_squared_error']].hvplot()

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [51]:
model_df[['loss', 'val_loss']].hvplot(

)

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [43]:
predictions = nn.predict(X_test)
# predictions = nn.predict(X_test.sort_index(ascending=True))

2/2 [==============================] - 0s 3ms/step


In [44]:
# R2 score from test
test_r2 = r2_score(y_test.values, predictions)
# test_r2 = r2_score(y_test.sort_index(ascending=True).values, predictions)
test_r2

0.9959060813024931

In [45]:
all_values_pred = nn.predict(X)
all_values_pred.shape

6/6 [==============================] - 0s 2ms/step


(176, 161)

In [46]:
all_feats_pred = nn.predict(X)
all_feats_pred_df = pd.DataFrame(all_feats_pred, columns=y.columns, index=X.index)
all_preds_feats_scaled_df = pd.concat([all_feats_pred_df, X], axis=1)
all_preds_feats_descaled = all_scaler.inverse_transform(all_preds_feats_scaled_df)
all_preds_feats_descaled_df = pd.DataFrame(all_preds_feats_descaled, columns=all_preds_feats_scaled_df.columns, index=all_preds_feats_scaled_df.index)
all_preds_descaled_df = all_preds_feats_descaled_df[targets]
all_preds_descaled_df.columns = ['PRED_'+col for col in all_preds_descaled_df.columns]
all_preds_descaled_df
# all_preds_feats_descaled_df
# all_pred_real = all_values_scaled_df.copy()
# all_pred_real['Composite'] = all_values_pred
# all_values_descaled = all_scaler.inverse_transform(all_pred_real)
# all_values_descaled_df = pd.DataFrame(all_values_descaled, columns=all_values_scaled_df.columns, index=all_values_scaled_df.index)
# all_values_descaled_df
# all_values_descaled_df['Predicted'] = all_values_descaled_df['Composite']
# all_values_descaled_df['Composite'] = all_values['Composite']
# all_values_descaled_df

6/6 [==============================] - 0s 2ms/step


PRED_Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                        
2008-06-01                                  162870.147019   
2008-07-01                                  162065.824609   
2008-08-01                                  165517.522743   
2008-09-01                                  165755.562798   
2008-10-01                                  161992.878444   
...                                                   ...   
2022-09-01                                  519545.598281   
2022-10-01                                  512152.287392   
2022-11-01                                  520943.723842   
2022-12-01                                  501620.074191   
2023-01-01                                  514069.923544   

            PRED_Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                            
2008-06-01                                      164788.258732   
2008-07-01                                      162634.392129   
2008-08-01                                      166467.712778   
2008-09-01                                      167227.190374   
2008-10-01                                      164400.132762   
...                                                       ...   
2022-09-01                                      512769.232468   
2022-10-01                                      505402.034219   
2022-11-01                                      517673.220744   
2022-12-01                                      500029.303066   
2023-01-01                                      514028.098853   

            PRED_One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                         
2008-06-01                                   154211.983274   
2008-07-01                                   153649.121166   
2008-08-01                                   157041.576723   
2008-09-01                                   156828.998394   
2008-10-01                                   153371.525173   
...                                                    ...   
2022-09-01                                   523471.727351   
2022-10-01                                   519859.380093   
2022-11-01                                   527524.202020   
2022-12-01                                   512521.188153   
2023-01-01                                   525825.664924   

            PRED_Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                         
2008-06-01                                   185712.781814   
2008-07-01                                   185669.986468   
2008-08-01                                   188605.549329   
2008-09-01                                   188096.885356   
2008-10-01                                   190133.513576   
...                                                    ...   
2022-09-01                                   486893.432266   
2022-10-01                                   470608.748680   
2022-11-01                                   483146.176013   
2022-12-01                                   455663.317480   
2023-01-01                                   473535.182820   

            PRED_Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                      
2008-06-01                                246065.988012   
2008-07-01                                243191.308133   
2008-08-01                                252084.946666   
2008-09-01                                252327.016840   
2008-10-01                                249511.643101   
...                                                 ...   
2022-09-01                                832073.203846   
2022-10-01                                810564.726965   
2022-11-01                                816250.929839   
2022-12-01                                773020.581654   
2023-01-01                                787565.4

In [47]:
bancroft_pred_compare_df = pd.concat([all_preds_descaled_df.loc[:,'PRED_Composite_Benchmark_SA_BANCROFT_AND_AREA'], all_values.loc[:,'Composite_Benchmark_SA_BANCROFT_AND_AREA']], axis=1)
bancroft_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [48]:
oakville_pred_compare_df = pd.concat([all_preds_descaled_df.loc[:,'PRED_Two_Storey_Benchmark_SA_OAKVILLE_MILTON'], all_values.loc[:,'Two_Storey_Benchmark_SA_OAKVILLE_MILTON']], axis=1)
oakville_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [32]:
all_targets_pred_compare_df = pd.concat([all_preds_descaled_df, all_values[targets]], axis=1)
all_targets_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [33]:
nn.save(Path(f"./Models/nn_in{n_input_feats}_relu{hidden_nodes_layer1}_relu{hidden_nodes_layer2}_relu{hidden_nodes_layer3}_out{n_outputs}_r2score{test_r2}_region_bldg.h5"))